In [62]:
# %load agent.py
import random
import math
from environment import Agent, Environment
from planner import RoutePlanner
from simulator import Simulator

class LearningAgent(Agent):
    """ An agent that learns to drive in the Smartcab world.
        This is the object you will be modifying. """ 

    def __init__(self, env, learning=False, epsilon=1.0, alpha=0.5):
        super(LearningAgent, self).__init__(env)     # Set the agent in the evironment 
        self.planner = RoutePlanner(self.env, self)  # Create a route planner
        self.valid_actions = self.env.valid_actions  # The set of valid actions

        # Set parameters of the learning agent
        self.learning = learning # Whether the agent is expected to learn
        self.Q = dict()          # Create a Q-table which will be a dictionary of tuples
        self.epsilon = epsilon   # Random exploration factor
        self.alpha = alpha       # Learning factor

        ###########
        ## TO DO ##
        ###########
        # Set any additional class parameters as needed
        self.n = 1


    def reset(self, destination=None, testing=False):
        """ The reset function is called at the beginning of each trial.
            'testing' is set to True if testing trials are being used
            once training trials have completed. """

        # Select the destination as the new location to route to
        self.planner.route_to(destination)
        
        ########### 
        ## TO DO ##
        ###########
        # Update epsilon using a decay function of your choice
        # Update additional class parameters as needed
        # If 'testing' is True, set epsilon and alpha to 0
        
#         self.epsilon = self.epsilon - 0.05
        self.epsilon = math.cos(math.pi/2/1000 * self.n)
#         self.epsilon = math.exp(-4*self.n/800.0)
#         self.epsilon -= 1.0/600
    
        self.n += 1
        
        if testing:
            self.epsilon = 0
            self.alpha = 0

        return None

    def build_state(self):
        """ The build_state function is called when the agent requests data from the 
            environment. The next waypoint, the intersection inputs, and the deadline 
            are all features available to the agent. """

        # Collect data about the environment
        waypoint = self.planner.next_waypoint() # The next waypoint 
        inputs = self.env.sense(self)           # Visual input - intersection light and traffic
        deadline = self.env.get_deadline(self)  # Remaining deadline

        ########### 
        ## TO DO ##
        ###########
        # Set 'state' as a tuple of relevant data for the agent        
        state = (inputs['light'], inputs['left'], inputs['oncoming'], inputs['right'], waypoint)

        return state


    def get_maxQ(self, state):
        """ The get_max_Q function is called when the agent is asked to find the
            maximum Q-value of all actions based on the 'state' the smartcab is in. """

        ########### 
        ## TO DO ##
        ###########
        # Calculate the maximum Q-value of all actions for a given state

        maxQ=max(self.Q[state].values())

        return maxQ


    def createQ(self, state):
        """ The createQ function is called when a state is generated by the agent. """

        ###########
        ## TO DO ##
        ###########
        # When learning, check if the 'state' is not in the Q-table
        # If it is not, create a new dictionary for that state
        #   Then, for each action available, set the initial Q-value to 0.0

        if self.learning:
            if state not in self.Q:
                self.Q[state] = dict()
                for act in self.valid_actions:
                    self.Q[state][act]=0.0
        return


    def choose_action(self, state):
        """ The choose_action function is called when the agent is asked to choose
            which action to take, based on the 'state' the smartcab is in. """

        # Set the agent state and default action
        self.state = state
        self.next_waypoint = self.planner.next_waypoint()
        
        if self.learning:
            if random.random < self.epsilon:
                action = random.choice(self.valid_actions)
            else:
                maxQ = self.get_maxQ(self.state)
                action = random.choice([act for act, value in self.Q[self.state].items() if value==maxQ])
        else:
            action = random.choice(self.valid_actions)
            
        ########### 
        ## TO DO ##
        ###########
        # When not learning, choose a random action
        # When learning, choose a random action with 'epsilon' probability
        #   Otherwise, choose an action with the highest Q-value for the current state
 
        return action


    def learn(self, state, action, reward):
        """ The learn function is called after the agent completes an action and
            receives an award. This function does not consider future rewards 
            when conducting learning. """

        ###########
        ## TO DO ##
        ###########
        # When learning, implement the value iteration update rule
        #   Use only the learning rate 'alpha' (do not use the discount factor 'gamma')

        if self.learning:
            self.Q[state][action] = (1-self.alpha)*self.Q[state][action] + self.alpha*reward
            
        return


    def update(self):
        """ The update function is called when a time step is completed in the 
            environment for a given trial. This function will build the agent
            state, choose an action, receive a reward, and learn if enabled. """

        state = self.build_state()          # Get current state
        self.createQ(state)                 # Create 'state' in Q-table
        action = self.choose_action(state)  # Choose an action
        reward = self.env.act(self, action) # Receive a reward
        self.learn(state, action, reward)   # Q-learn

        return
        

def run():
    """ Driving function for running the simulation. 
        Press ESC to close the simulation, or [SPACE] to pause the simulation. """

    ##############
    # Create the environment
    # Flags:
    #   verbose     - set to True to display additional output from the simulation
    #   num_dummies - discrete number of dummy agents in the environment, default is 100
    #   grid_size   - discrete number of intersections (columns, rows), default is (8, 6)
    env = Environment()
    
    ##############
    # Create the driving agent
    # Flags:
    #   learning   - set to True to force the driving agent to use Q-learning
    #    * epsilon - continuous value for the exploration factor, default is 1
    #    * alpha   - continuous value for the learning rate, default is 0.5
    agent = env.create_agent(LearningAgent, learning=True)
    
    ##############
    # Follow the driving agent
    # Flags:
    #   enforce_deadline - set to True to enforce a deadline metric
    env.set_primary_agent(agent, enforce_deadline=True)

    ##############
    # Create the simulation
    # Flags:
    #   update_delay - continuous time (in seconds) between actions, default is 2.0 seconds
    #   display      - set to False to disable the GUI if PyGame is enabled
    #   log_metrics  - set to True to log trial and simulation results to /logs
    #   optimized    - set to True to change the default log file name
    sim = Simulator(env, update_delay=0, log_metrics=True, optimized=True, display=False)
    
    ##############
    # Run the simulator
    # Flags:
    #   tolerance  - epsilon tolerance before beginning testing, default is 0.05 
    #   n_test     - discrete number of testing trials to perform, default is 0
    sim.run(n_test=50, tolerance=0.03)


if __name__ == '__main__':
    run()


/-------------------------
| Training trial 1
\-------------------------


/-------------------
| Step 0 Results
\-------------------

Agent previous state: ('red', None, None, None, 'left')
Agent attempted driving left through a red light. (rewarded -9.62)
95% of time remaining to reach destination.

/-------------------
| Step 1 Results
\-------------------

Agent previous state: ('red', None, 'left', None, 'left')
Agent attempted driving left through a red light. (rewarded -9.47)
90% of time remaining to reach destination.

/-------------------
| Step 2 Results
\-------------------

Agent previous state: ('red', None, 'left', None, 'left')
Agent properly idled at a red light. (rewarded 2.56)
85% of time remaining to reach destination.

/-------------------
| Step 3 Results
\-------------------

Agent previous state: ('green', None, 'left', None, 'left')
Agent drove right instead of left. (rewarded 1.34)
80% of time remaining to reach destination.

/-------------------
| Step 4 Resu

Agent previous state: ('red', None, 'left', None, 'left')
Agent properly idled at a red light. (rewarded 2.41)
75% of time remaining to reach destination.

/-------------------
| Step 5 Results
\-------------------

Agent previous state: ('green', None, 'left', None, 'left')
Agent drove right instead of left. (rewarded 1.71)
70% of time remaining to reach destination.

/-------------------
| Step 6 Results
\-------------------

Agent previous state: ('green', 'right', None, 'forward', 'left')
Agent followed the waypoint left. (rewarded 2.60)
65% of time remaining to reach destination.

/-------------------
| Step 7 Results
\-------------------

Agent previous state: ('red', None, None, None, 'left')
Agent drove right instead of left. (rewarded 0.08)
60% of time remaining to reach destination.

/-------------------
| Step 8 Results
\-------------------

Agent previous state: ('red', None, None, None, 'right')
Agent followed the waypoint right. (rewarded 2.22)
55% of time remaining to re

Agent previous state: ('red', None, 'left', None, 'left')
Agent properly idled at a red light. (rewarded 2.30)
83% of time remaining to reach destination.

/-------------------
| Step 5 Results
\-------------------

Agent previous state: ('green', None, 'left', None, 'left')
Agent drove forward instead of left. (rewarded 1.90)
80% of time remaining to reach destination.

/-------------------
| Step 6 Results
\-------------------

Agent previous state: ('red', 'left', None, 'left', 'forward')
Agent attempted driving forward through a red light. (rewarded -10.94)
77% of time remaining to reach destination.

/-------------------
| Step 7 Results
\-------------------

Agent previous state: ('red', None, None, 'forward', 'forward')
Agent attempted driving forward through a red light with traffic and cause a major accident. (rewarded -40.80)
73% of time remaining to reach destination.

/-------------------
| Step 8 Results
\-------------------

Agent previous state: ('red', None, 'right', No

Agent previous state: ('green', None, None, None, 'forward')
Agent followed the waypoint forward. (rewarded 1.21)
76% of time remaining to reach destination.

/-------------------
| Step 6 Results
\-------------------

Agent previous state: ('red', None, None, None, 'right')
Agent followed the waypoint right. (rewarded 2.11)
72% of time remaining to reach destination.

/-------------------
| Step 7 Results
\-------------------

Agent previous state: ('red', None, None, 'left', 'forward')
Agent properly idled at a red light. (rewarded 1.50)
68% of time remaining to reach destination.

/-------------------
| Step 8 Results
\-------------------

Agent previous state: ('red', 'left', 'forward', 'forward', 'forward')
Agent properly idled at a red light. (rewarded 1.53)
64% of time remaining to reach destination.

/-------------------
| Step 9 Results
\-------------------

Agent previous state: ('green', None, 'forward', 'forward', 'forward')
Agent followed the waypoint forward. (rewarded 2.

Agent previous state: ('red', 'forward', None, 'right', 'left')
Agent attempted driving right through traffic and cause a minor accident. (rewarded -20.79)
48% of time remaining to reach destination.

/-------------------
| Step 13 Results
\-------------------

Agent previous state: ('green', None, None, None, 'left')
Agent followed the waypoint left. (rewarded 1.63)
44% of time remaining to reach destination.

/-------------------
| Step 14 Results
\-------------------

Agent previous state: ('red', 'left', 'left', None, 'forward')
Agent drove right instead of forward. (rewarded 0.24)
40% of time remaining to reach destination.

/-------------------
| Step 15 Results
\-------------------

Agent previous state: ('red', None, 'left', None, 'left')
Agent properly idled at a red light. (rewarded 1.86)
36% of time remaining to reach destination.

/-------------------
| Step 16 Results
\-------------------

Agent previous state: ('red', 'right', 'left', None, 'left')
Agent attempted driving

...

Agent previous state: ('red', None, 'left', 'forward', 'left')
Agent properly idled at a red light. (rewarded 2.52)
57% of time remaining to reach destination.

/-------------------
| Step 13 Results
\-------------------

Agent previous state: ('green', None, 'left', None, 'left')
Agent followed the waypoint left. (rewarded 1.89)
53% of time remaining to reach destination.

/-------------------
| Step 14 Results
\-------------------

Agent previous state: ('green', None, None, None, 'left')
Agent followed the waypoint left. (rewarded 1.70)
50% of time remaining to reach destination.

Trial Completed!
Agent reached the destination.

/-------------------------
| Testing trial 37
\-------------------------


/-------------------
| Step 0 Results
\-------------------

Agent previous state: ('red', 'left', 'forward', None, 'forward')
Agent drove right instead of forward. (rewarded 1.64)
96% of time remaining to reach destination.

/-------------------
| Step 1 Results
\-------------------



Agent previous state: ('green', 'forward', None, 'forward', 'right')
Agent followed the waypoint right. (rewarded 2.38)
70% of time remaining to reach destination.

/-------------------
| Step 6 Results
\-------------------

Agent previous state: ('green', 'forward', 'left', None, 'forward')
Agent followed the waypoint forward. (rewarded 1.28)
65% of time remaining to reach destination.

Trial Completed!
Agent reached the destination.

/-------------------------
| Testing trial 40
\-------------------------


/-------------------
| Step 0 Results
\-------------------

Agent previous state: ('green', None, 'forward', 'right', 'right')
Agent followed the waypoint right. (rewarded 2.81)
96% of time remaining to reach destination.

/-------------------
| Step 1 Results
\-------------------

Agent previous state: ('red', None, None, None, 'forward')
Agent properly idled at a red light. (rewarded 1.24)
92% of time remaining to reach destination.

/-------------------
| Step 2 Results
\------

Agent previous state: ('red', None, 'left', None, 'forward')
Agent properly idled at a red light. (rewarded 0.75)
35% of time remaining to reach destination.

/-------------------
| Step 13 Results
\-------------------

Agent previous state: ('green', None, 'left', 'right', 'forward')
Agent drove right instead of forward. (rewarded -0.08)
30% of time remaining to reach destination.

/-------------------
| Step 14 Results
\-------------------

Agent previous state: ('green', None, None, None, 'left')
Agent followed the waypoint left. (rewarded 2.19)
25% of time remaining to reach destination.

/-------------------
| Step 15 Results
\-------------------

Agent previous state: ('green', 'right', 'left', None, 'forward')
Agent followed the waypoint forward. (rewarded 1.59)
20% of time remaining to reach destination.

/-------------------
| Step 16 Results
\-------------------

Agent previous state: ('red', None, 'forward', 'right', 'left')
Agent properly idled at a red light. (rewarded 2.1

Agent previous state: ('red', 'forward', 'left', 'forward', 'forward')
Agent properly idled at a red light. (rewarded 2.23)
90% of time remaining to reach destination.

/-------------------
| Step 2 Results
\-------------------

Agent previous state: ('red', 'right', 'left', 'left', 'forward')
Agent properly idled at a red light. (rewarded 2.96)
85% of time remaining to reach destination.

/-------------------
| Step 3 Results
\-------------------

Agent previous state: ('red', None, 'left', None, 'forward')
Agent properly idled at a red light. (rewarded 1.70)
80% of time remaining to reach destination.

/-------------------
| Step 4 Results
\-------------------

Agent previous state: ('red', None, 'left', None, 'forward')
Agent properly idled at a red light. (rewarded 2.08)
75% of time remaining to reach destination.

/-------------------
| Step 5 Results
\-------------------

Agent previous state: ('green', None, 'left', None, 'forward')
Agent followed the waypoint forward. (rewarded

Agent previous state: ('red', None, 'forward', None, 'forward')
Agent properly idled at a red light. (rewarded 2.44)
87% of time remaining to reach destination.

/-------------------
| Step 4 Results
\-------------------

Agent previous state: ('red', None, 'forward', None, 'forward')
Agent properly idled at a red light. (rewarded 1.52)
83% of time remaining to reach destination.

/-------------------
| Step 5 Results
\-------------------

Agent previous state: ('green', 'right', 'forward', None, 'forward')
Agent followed the waypoint forward. (rewarded 1.21)
80% of time remaining to reach destination.

/-------------------
| Step 6 Results
\-------------------

Agent previous state: ('red', 'right', 'forward', None, 'forward')
Agent properly idled at a red light. (rewarded 1.74)
77% of time remaining to reach destination.

/-------------------
| Step 7 Results
\-------------------

Agent previous state: ('red', None, 'forward', None, 'forward')
Agent properly idled at a red light. (re